# **COVID-19 Analysis, Visualization,Maps and Animation**

## *imports Library and Data*

In [40]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from matplotlib import ticker 
import pycountry_convert as pc
import folium
import branca
from datetime import datetime, timedelta,date
from scipy.interpolate import make_interp_spline, BSpline
import plotly.express as px
import json, requests
%matplotlib inline
import cufflinks as cf
import plotly as py

In [41]:
#!pip install pycountry_convert

In [42]:
#make directory for plots
!mkdir plots
plots = "plots" 

In [43]:
#  Datasets
df_confirmed= pd.read_csv('https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_confirmed_global.csv')
df_deaths = pd.read_csv('https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_deaths_global.csv')
df_covid19 = pd.read_csv("https://raw.githubusercontent.com/CSSEGISandData/COVID-19/web-data/data/cases_country.csv")
df_table = pd.read_csv("https://raw.githubusercontent.com/CSSEGISandData/COVID-19/web-data/data/cases_time.csv",parse_dates=['Last_Update'])


In [44]:
df_covid19.head(2)

Country_Region          Last_Update      Lat     Long_  Confirmed  Deaths  \
0      Australia  2020-06-15 23:33:10 -25.0000  133.0000     7347.0   102.0   
1        Austria  2020-06-15 23:33:10  47.5162   14.5501    17135.0   678.0   

   Recovered  Active  Incident_Rate  People_Tested  People_Hospitalized  \
0     6851.0   394.0      28.857371            NaN                  NaN   
1    16066.0   391.0     190.253597            NaN                  NaN   

   Mortality_Rate  UID ISO3  
0        1.388322   36  AUS  
1        3.956814   40  AUT

## **Data Preprocessing** 

In [45]:
df_confirmed = df_confirmed.rename(columns={"Province/State":"state","Country/Region": "country"})
df_deaths = df_deaths.rename(columns={"Province/State":"state","Country/Region": "country"})
df_covid19 = df_covid19.rename(columns={"Country_Region": "country"})
df_covid19["Active"] = df_covid19["Confirmed"]-df_covid19["Recovered"]-df_covid19["Deaths"]
df_covid19.head(2)

country          Last_Update      Lat     Long_  Confirmed  Deaths  \
0  Australia  2020-06-15 23:33:10 -25.0000  133.0000     7347.0   102.0   
1    Austria  2020-06-15 23:33:10  47.5162   14.5501    17135.0   678.0   

   Recovered  Active  Incident_Rate  People_Tested  People_Hospitalized  \
0     6851.0   394.0      28.857371            NaN                  NaN   
1    16066.0   391.0     190.253597            NaN                  NaN   

   Mortality_Rate  UID ISO3  
0        1.388322   36  AUS  
1        3.956814   40  AUT

In [46]:
# Changing the conuntry names as required by pycountry_convert Lib
df_confirmed.loc[df_confirmed['country'] == "US", "country"] = "USA"
df_deaths.loc[df_deaths['country'] == "US", "country"] = "USA"
df_covid19.loc[df_covid19['country'] == "US", "country"] = "USA"
df_table.loc[df_table['Country_Region'] == "US", "Country_Region"] = "USA"
df_table.head(2)

Country_Region Last_Update  Confirmed  Deaths  Recovered  Active  \
0    Afghanistan  2020-01-22          0       0        NaN     NaN   
1    Afghanistan  2020-01-23          0       0        NaN     NaN   

   Delta_Confirmed  Delta_Recovered  Incident_Rate  People_Tested  \
0              0.0              NaN            0.0            NaN   
1              0.0              NaN            0.0            NaN   

   People_Hospitalized Province_State  FIPS  UID iso3 Report_Date_String  
0                  NaN            NaN   NaN    4  AFG         2020/01/22  
1                  NaN            NaN   NaN    4  AFG         2020/01/23

In [47]:
df_confirmed.loc[df_confirmed['country'] == 'Korea, South', "country"] = 'South Korea'
df_deaths.loc[df_deaths['country'] == 'Korea, South', "country"] = 'South Korea'
df_covid19.loc[df_covid19['country'] == "Korea, South", "country"] = "South Korea"
df_table.loc[df_table['Country_Region'] == "Korea, South", "Country_Region"] = "South Korea"
df_table.head(2)

Country_Region Last_Update  Confirmed  Deaths  Recovered  Active  \
0    Afghanistan  2020-01-22          0       0        NaN     NaN   
1    Afghanistan  2020-01-23          0       0        NaN     NaN   

   Delta_Confirmed  Delta_Recovered  Incident_Rate  People_Tested  \
0              0.0              NaN            0.0            NaN   
1              0.0              NaN            0.0            NaN   

   People_Hospitalized Province_State  FIPS  UID iso3 Report_Date_String  
0                  NaN            NaN   NaN    4  AFG         2020/01/22  
1                  NaN            NaN   NaN    4  AFG         2020/01/23

In [48]:
df_confirmed.loc[df_confirmed['country'] == 'Taiwan*', "country"] = 'Taiwan'
df_deaths.loc[df_deaths['country'] == 'Taiwan*', "country"] = 'Taiwan'
df_covid19.loc[df_covid19['country'] == "Taiwan*", "country"] = "Taiwan"
df_table.loc[df_table['Country_Region'] == "Taiwan*", "Country_Region"] = "Taiwan"
df_table.head(2)

Country_Region Last_Update  Confirmed  Deaths  Recovered  Active  \
0    Afghanistan  2020-01-22          0       0        NaN     NaN   
1    Afghanistan  2020-01-23          0       0        NaN     NaN   

   Delta_Confirmed  Delta_Recovered  Incident_Rate  People_Tested  \
0              0.0              NaN            0.0            NaN   
1              0.0              NaN            0.0            NaN   

   People_Hospitalized Province_State  FIPS  UID iso3 Report_Date_String  
0                  NaN            NaN   NaN    4  AFG         2020/01/22  
1                  NaN            NaN   NaN    4  AFG         2020/01/23

In [49]:
df_confirmed.loc[df_confirmed['country'] == 'Congo (Kinshasa)', "country"] = 'Democratic Republic of the Congo'
df_deaths.loc[df_deaths['country'] == 'Congo (Kinshasa)', "country"] = 'Democratic Republic of the Congo'
df_covid19.loc[df_covid19['country'] == "Congo (Kinshasa)", "country"] = "Democratic Republic of the Congo"
df_table.loc[df_table['Country_Region'] == "Congo (Kinshasa)", "Country_Region"] = "Democratic Republic of the Congo"
df_table.head(2)

Country_Region Last_Update  Confirmed  Deaths  Recovered  Active  \
0    Afghanistan  2020-01-22          0       0        NaN     NaN   
1    Afghanistan  2020-01-23          0       0        NaN     NaN   

   Delta_Confirmed  Delta_Recovered  Incident_Rate  People_Tested  \
0              0.0              NaN            0.0            NaN   
1              0.0              NaN            0.0            NaN   

   People_Hospitalized Province_State  FIPS  UID iso3 Report_Date_String  
0                  NaN            NaN   NaN    4  AFG         2020/01/22  
1                  NaN            NaN   NaN    4  AFG         2020/01/23

In [50]:
df_confirmed.loc[df_confirmed['country'] == "Cote d'Ivoire", "country"] = "Côte d'Ivoire"
df_deaths.loc[df_deaths['country'] == "Cote d'Ivoire", "country"] = "Côte d'Ivoire"
df_covid19.loc[df_covid19['country'] == "Cote d'Ivoire", "country"] = "Côte d'Ivoire"
df_table.loc[df_table['Country_Region'] == "Cote d'Ivoire", "Country_Region"] = "Côte d'Ivoire"
df_table.head(2)

Country_Region Last_Update  Confirmed  Deaths  Recovered  Active  \
0    Afghanistan  2020-01-22          0       0        NaN     NaN   
1    Afghanistan  2020-01-23          0       0        NaN     NaN   

   Delta_Confirmed  Delta_Recovered  Incident_Rate  People_Tested  \
0              0.0              NaN            0.0            NaN   
1              0.0              NaN            0.0            NaN   

   People_Hospitalized Province_State  FIPS  UID iso3 Report_Date_String  
0                  NaN            NaN   NaN    4  AFG         2020/01/22  
1                  NaN            NaN   NaN    4  AFG         2020/01/23

In [51]:
df_confirmed.loc[df_confirmed['country'] == "Reunion", "country"] = "Réunion"
df_deaths.loc[df_deaths['country'] == "Reunion", "country"] = "Réunion"
df_covid19.loc[df_covid19['country'] == "Reunion", "country"] = "Réunion"
df_table.loc[df_table['Country_Region'] == "Reunion", "Country_Region"] = "Réunion"
df_table.head(2)

Country_Region Last_Update  Confirmed  Deaths  Recovered  Active  \
0    Afghanistan  2020-01-22          0       0        NaN     NaN   
1    Afghanistan  2020-01-23          0       0        NaN     NaN   

   Delta_Confirmed  Delta_Recovered  Incident_Rate  People_Tested  \
0              0.0              NaN            0.0            NaN   
1              0.0              NaN            0.0            NaN   

   People_Hospitalized Province_State  FIPS  UID iso3 Report_Date_String  
0                  NaN            NaN   NaN    4  AFG         2020/01/22  
1                  NaN            NaN   NaN    4  AFG         2020/01/23

In [52]:
df_confirmed.loc[df_confirmed['country'] == 'Congo (Brazzaville)', "country"] = 'Republic of the Congo'
df_deaths.loc[df_deaths['country'] == 'Congo (Brazzaville)', "country"] = 'Republic of the Congo'
df_covid19.loc[df_covid19['country'] == "Congo (Brazzaville)", "country"] = "Republic of the Congo"
df_table.loc[df_table['Country_Region'] == "Congo (Brazzaville)", "Country_Region"] = "Republic of the Congo"
df_table.head(2)

Country_Region Last_Update  Confirmed  Deaths  Recovered  Active  \
0    Afghanistan  2020-01-22          0       0        NaN     NaN   
1    Afghanistan  2020-01-23          0       0        NaN     NaN   

   Delta_Confirmed  Delta_Recovered  Incident_Rate  People_Tested  \
0              0.0              NaN            0.0            NaN   
1              0.0              NaN            0.0            NaN   

   People_Hospitalized Province_State  FIPS  UID iso3 Report_Date_String  
0                  NaN            NaN   NaN    4  AFG         2020/01/22  
1                  NaN            NaN   NaN    4  AFG         2020/01/23

In [53]:
df_confirmed.loc[df_confirmed['country'] == 'Bahamas, The', "country"] = 'Bahamas'
df_deaths.loc[df_deaths['country'] == 'Bahamas, The', "country"] = 'Bahamas'
df_covid19.loc[df_covid19['country'] == "Bahamas, The", "country"] = "Bahamas"
df_table.loc[df_table['Country_Region'] == "Bahamas, The", "Country_Region"] = "Bahamas"
df_table.head(2)

Country_Region Last_Update  Confirmed  Deaths  Recovered  Active  \
0    Afghanistan  2020-01-22          0       0        NaN     NaN   
1    Afghanistan  2020-01-23          0       0        NaN     NaN   

   Delta_Confirmed  Delta_Recovered  Incident_Rate  People_Tested  \
0              0.0              NaN            0.0            NaN   
1              0.0              NaN            0.0            NaN   

   People_Hospitalized Province_State  FIPS  UID iso3 Report_Date_String  
0                  NaN            NaN   NaN    4  AFG         2020/01/22  
1                  NaN            NaN   NaN    4  AFG         2020/01/23

In [54]:
df_confirmed.loc[df_confirmed['country'] == 'Gambia, The', "country"] = 'Gambia'
df_deaths.loc[df_deaths['country'] == 'Gambia, The', "country"] = 'Gambia'
df_covid19.loc[df_covid19['country'] == "Gambia, The", "country"] = "Gambia"
df_table.loc[df_table['Country_Region'] == "Gambia", "Country_Region"] = "Gambia"
df_table.head(2)

Country_Region Last_Update  Confirmed  Deaths  Recovered  Active  \
0    Afghanistan  2020-01-22          0       0        NaN     NaN   
1    Afghanistan  2020-01-23          0       0        NaN     NaN   

   Delta_Confirmed  Delta_Recovered  Incident_Rate  People_Tested  \
0              0.0              NaN            0.0            NaN   
1              0.0              NaN            0.0            NaN   

   People_Hospitalized Province_State  FIPS  UID iso3 Report_Date_String  
0                  NaN            NaN   NaN    4  AFG         2020/01/22  
1                  NaN            NaN   NaN    4  AFG         2020/01/23

# ---------------------------------------#

In [55]:
# getting all countries
countries = np.asarray(df_confirmed["country"])
countries1 = np.asarray(df_covid19["country"])
# Continent_code to Continent_names
continents = {
    'NA': 'North America',
    'SA': 'South America', 
    'AS': 'Asia',
    'OC': 'Australia',
    'AF': 'Africa',
    'EU' : 'Europe',
    'na' : 'Others'
}

In [56]:
# Defininng Function for getting continent code for country.
def country_to_continent_code(country):
    try:
        return pc.country_alpha2_to_continent_code(pc.country_name_to_country_alpha2(country))
    except :
        return 'na'

#Collecting Continent Information
df_confirmed.insert(2,"continent", [continents[country_to_continent_code(country)] for country in countries[:]])
df_deaths.insert(2,"continent",  [continents[country_to_continent_code(country)] for country in countries[:]])
df_covid19.insert(1,"continent",  [continents[country_to_continent_code(country)] for country in countries1[:]])
df_table.insert(1,"continent",  [continents[country_to_continent_code(country)] for country in df_table["Country_Region"].values])

In [57]:
df_table = df_table[df_table["continent"] != "Others"]

In [58]:
df_table.head(2)

Country_Region continent Last_Update  Confirmed  Deaths  Recovered  Active  \
0    Afghanistan      Asia  2020-01-22          0       0        NaN     NaN   
1    Afghanistan      Asia  2020-01-23          0       0        NaN     NaN   

   Delta_Confirmed  Delta_Recovered  Incident_Rate  People_Tested  \
0              0.0              NaN            0.0            NaN   
1              0.0              NaN            0.0            NaN   

   People_Hospitalized Province_State  FIPS  UID iso3 Report_Date_String  
0                  NaN            NaN   NaN    4  AFG         2020/01/22  
1                  NaN            NaN   NaN    4  AFG         2020/01/23

In [59]:
df_deaths[df_deaths["continent" ]== 'Others']

state             country continent        Lat        Long  1/22/20  \
88    NaN    Diamond Princess    Others   0.000000    0.000000        0   
127   NaN            Holy See    Others  41.902900   12.453400        0   
236   NaN         Timor-Leste    Others  -8.874217  125.727539        0   
240   NaN  West Bank and Gaza    Others  31.952200   35.233200        0   
246   NaN              Kosovo    Others  42.602636   20.902977        0   
247   NaN               Burma    Others  21.916200   95.956000        0   
251   NaN          MS Zaandam    Others   0.000000    0.000000        0   
260   NaN      Western Sahara    Others  24.215500  -12.885800        0   

     1/23/20  1/24/20  1/25/20  1/26/20  ...  6/5/20  6/6/20  6/7/20  6/8/20  \
88         0        0        0        0  ...      13      13      13      13   
127        0        0        0        0  ...       0       0       0       0   
236        0        0        0        0  ...       0       0       0       0   
240        0        0        0        0  ...       3       3       3       3   
246        0        0        0        0  ...      30      30      30      31   
247        0        0        0        0  ...       6       6       6       6   
251        0        0        0        0  ...       2       2       2       2   
260        0        0        0        0  ...       1       1       1       1   

     6/9/20  6/10/20  6/11/20  6/12/20  6/13/20  6/14/20  
88       13       13       13       13       13       13  
127       0        0        0        0        0        0  
236       0        0        0        0        0        0  
240       3        3        3        3        3        3  
246      31       31       31       31       32       32  
247       6        6        6        6        6        6  
251       2        2        2        2        2        2  
260       1        1        1        1        1        1  

[8 rows x 150 columns]

In [60]:
df_confirmed = df_confirmed.replace(np.nan, '', regex=True)
df_deaths = df_deaths.replace(np.nan, '', regex=True)

## General info on Globe 

In [61]:
df_countries_cases = df_covid19.copy().drop(['Lat','Long_','continent','Last_Update'],axis =1)
df_countries_cases.index = df_countries_cases["country"]
df_countries_cases = df_countries_cases.drop(['country'],axis=1)

df_continents_cases = df_covid19.copy().drop(['Lat','Long_','country','Last_Update'],axis =1)
df_continents_cases = df_continents_cases.groupby(["continent"]).sum()

In [62]:
pd.DataFrame(df_countries_cases.sum()).transpose().style.background_gradient(cmap='Wistia',axis=1)

In [63]:
df_continents_cases.style.background_gradient(cmap='Wistia')

In [64]:
df_countries_cases.sort_values('Confirmed', ascending= False).style.background_gradient(cmap='Wistia')


/Users/resitkadir/opt/anaconda3/lib/python3.7/site-packages/matplotlib/colors.py:527: RuntimeWarning:

invalid value encountered in less

/Users/resitkadir/opt/anaconda3/lib/python3.7/site-packages/pandas/io/formats/style.py:1089: RuntimeWarning:

All-NaN slice encountered

/Users/resitkadir/opt/anaconda3/lib/python3.7/site-packages/pandas/io/formats/style.py:1090: RuntimeWarning:

All-NaN slice encountered



In [65]:
df_countries_cases.corr().style.background_gradient(cmap='Reds')

In [66]:
df_continents_cases.corr().style.background_gradient(cmap='Reds')

# *MAPS*

In [67]:
world_map = folium.Map(location=[0,0], tiles="cartodbpositron", zoom_start=1,max_zoom=6,min_zoom=1)

for i in range(0,len(df_confirmed)):
    folium.Circle(
        location=[df_confirmed.iloc[i]['Lat'], df_confirmed.iloc[i]['Long']],
        tooltip = "<h5 style='text-align:center;font-weight: bold'>"+df_confirmed.iloc[i]['country']+"</h5>"+
                    "<div style='text-align:center;'>"+str(np.nan_to_num(df_confirmed.iloc[i]['state']))+"</div>"+
                    "<hr style='margin:10px;'>"+
                    "<ul style='color: #444;list-style-type:circle;align-item:left;padding-left:20px;padding-right:20px'>"+
        "<li>Confirmed: "+str(df_confirmed.iloc[i,-1])+"</li>"+
        "<li>Deaths:   "+str(df_deaths.iloc[i,-1])+"</li>"+
        "<li>Mortality Rate:   "+str(np.round(df_deaths.iloc[i,-1]/(df_confirmed.iloc[i,-1]+1.00001)*100,2))+"</li>"+
        "</ul>"
        ,
        radius=(int((np.log(df_confirmed.iloc[i,-1]+1.00001)))+0.2)*50000,
        color='#ff6600',
        fill_color='#ff8533',
        fill=True).add_to(world_map)

world_map



In [28]:
#!pip install cufflinks

In [69]:

temp_df = pd.DataFrame(df_countries_cases['Confirmed'])
temp_df = temp_df.reset_index()
fig = px.choropleth(temp_df, locations="country",
                    color=np.log10(temp_df.iloc[:,-1]), # lifeExp is a column of gapminder
                    hover_name="country", # column to add to hover information
                    hover_data=["Confirmed"],
                    color_continuous_scale=px.colors.sequential.Plasma,locationmode="country names")
fig.update_geos(fitbounds="locations", visible=False)
fig.update_layout(title_text="Confirmed Cases Heat Map (Log Scale)")
fig.update_coloraxes(colorbar_title="Confirmed Cases(Log Scale)",colorscale="YlGnBu")
# fig.to_image("Global Heat Map confirmed.png")
fig.show()
py.offline.plot(fig,filename=plots+"/Confirmed Cases Heat MAp-logscale.html",auto_open =False)


'plots/Confirmed Cases Heat MAp-logscale.html'

In [70]:
temp_df = pd.DataFrame(df_countries_cases['Deaths'])
temp_df = temp_df.reset_index()
fig = px.choropleth(temp_df, locations="country",
                   
                    color=np.log10(temp_df.iloc[:,-1]+1), # lifeExp is a column of gapminder
                    hover_name="country", # column to add to hover information
                    hover_data=["Deaths"],
                    color_continuous_scale=px.colors.sequential.Plasma,locationmode="country names")
fig.update_geos(fitbounds="locations", visible=False)
fig.update_layout(title_text="Deaths Heat Map (Log Scale)")
fig.update_coloraxes(colorbar_title="Deaths (Log Scale)",colorscale="Reds")
# fig.to_image("Global Heat Map deaths.png")
fig.show()
py.offline.plot(fig,filename=plots+"/Death Cases Heat MAp-logscale.html",auto_open =False)



SyntaxError: invalid syntax (<ipython-input-70-484333edf39a>, line 14)

In [71]:
df_data = df_table.groupby(['Last_Update', 'Country_Region'])['Confirmed', 'Deaths'].max().reset_index()
df_data["Last_Update"] = pd.to_datetime( df_data["Last_Update"]).dt.strftime('%m/%d/%Y')

fig = px.scatter_geo(df_data, locations="Country_Region", locationmode='country names', 
                     color=np.power(df_data["Confirmed"],0.3)-2 , size= np.power(df_data["Confirmed"]+1,0.3)-1, hover_name="Country_Region",
                     hover_data=["Confirmed"],
                     range_color= [0, max(np.power(df_data["Confirmed"],0.3))], 
                     projection="natural earth", animation_frame="Last_Update", 
                     color_continuous_scale=px.colors.sequential.Plasma,
                     title='Spreading Animation'
                    )
fig.update_coloraxes(colorscale="hot")
fig.update(layout_coloraxis_showscale=False)
fig.show()
py.offline.plot(fig,filename=plots+"/Spreading animation.html",auto_open =False)

SyntaxError: invalid syntax (<ipython-input-71-0017da7e6d5c>, line 15)

In [74]:
df_data = df_table.groupby(['Last_Update', 'Country_Region'])['Confirmed', 'Deaths','continent'].max().reset_index()
df_data["Last_Update"] = pd.to_datetime( df_data["Last_Update"]).dt.strftime('%m/%d/%Y')

fig = px.scatter(df_data, y=df_data["Deaths"],
                    x= df_data["Confirmed"]+1,
                    range_y = [1,df_data["Deaths"].max()+1000],
                    range_x = [1,df_data["Confirmed"].max()+10000],
                    color= "continent", hover_name="Country_Region",
                    hover_data=["Confirmed","Deaths"],
                    range_color= [0, max(np.power(df_data["Confirmed"],0.3))], 
                    animation_frame="Last_Update", 
                    animation_group="Country_Region",
                    color_continuous_scale=px.colors.sequential.Viridis,
                    title='Deaths vs Cofirmed Cases of Each Countries Over Time',
                    size = np.power(df_data["Confirmed"]+1,0.3)-0.5,
                    size_max = 30,
                    log_x=True,
                    log_y=True,
                    height =700,
                    )
fig.update_coloraxes(colorscale="hot")
fig.update(layout_coloraxis_showscale=True)
fig.update_xaxes(title_text="Confirmed Cases (Log Scale)")
fig.update_yaxes(title_text="Deaths (Log Scale)")
fig.show()
py.offline.plot(fig,filename=plots+"/TimeLine on Death and Confirmed Cases.html",auto_open=False)

/Users/resitkadir/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: FutureWarning:

Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.



'plots/TimeLine on Death and Confirmed Cases.html'